# 509 Final Project

## Rsolve dependencies

## Globally import libraries

In [1]:
import numpy as np
import pandas as pd
import pymysql as mysql
import matplotlib.pyplot as plt
import os
import shutil
import re
import logging
import time
import zipfile
import requests
from bs4 import BeautifulSoup
import datetime
import re
import regex as rex
from collections import defaultdict, Counter
import random
#import mysql.connector

# Set pandas global options
pd.options.display.max_rows = 17

## Initiate MySQL connection

In [2]:
'''Set local environment variables to hide user name & password citation:
https://www.geeksforgeeks.org/how-to-hide-sensitive-credentials-using-python/'''

user_name = os.environ['MySQLUSRAC']
user_pass = os.environ['MySQLPWDAC']

# Instantiate connection
db_conn = mysql.connect(host='localhost',
                        port=int(3306),
                        user=user_name,
                        passwd=user_pass,
                        db='509_final_proj')

# Create a cursor object
cursor = db_conn.cursor()

In [3]:
tbl_names = pd.read_sql('SHOW TABLES', db_conn)

display(tbl_names)
print(type(tbl_names))

C:\Users\acarr\AppData\Local\Temp\ipykernel_19248\4193860975.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  tbl_names = pd.read_sql('SHOW TABLES', db_conn)


Tables_in_509_final_proj
0                 nar_temp
1            news_articles

<class 'pandas.core.frame.DataFrame'>


## Read URLs from MySQL table to perform web scraping

In [4]:
'''Set local environment variables to hide user name & password citation:
https://www.geeksforgeeks.org/how-to-hide-sensitive-credentials-using-python/'''

user_name = os.environ['MySQLUSRAC']
user_pass = os.environ['MySQLPWDAC']

# Instantiate connection
db_conn = mysql.connect(host='localhost',
                        port=int(3306),
                        user=user_name,
                        passwd=user_pass,
                        db='509_final_proj')

# Create a cursor object
cursor = db_conn.cursor()

In [5]:
nat_tbl_name = 'nar_temp'
nwa_tbl_name = 'news_articles'

In [6]:
text_query = f"SELECT url, article_text FROM {nwa_tbl_name}"
df = pd.read_sql(text_query, db_conn)

C:\Users\acarr\AppData\Local\Temp\ipykernel_19248\2936052196.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(text_query, db_conn)


In [7]:
print(df.head())
story_str000 = df['article_text'][0]
print(story_str000)

                                                 url  \
0  https://www.cnn.com/2023/05/26/homes/fitch-cre...   
1  https://www.cnn.com/2023/05/26/middleeast/iran...   
2  https://www.cnn.com/2023/05/26/sport/malaysian...   
3  https://www.cnn.com/2023/05/26/golf/amy-olson-...   
4  https://www.cnn.com/2023/05/26/us/banko-brown-...   

                                        article_text  
0  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
1  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
2  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
3  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
4  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
<!DOCTYPE html>
<html data-layout-uri="cms.cnn.com/_layouts/layout-with-rail/instances/business-article-v1@published" data-uri="cms.cnn.com/_pages/h_9062c752a61be2f44593768475f220e4@published" lang="en">
 <head>
  <style>
   body,h1,h2,h3,h4,h5{font-family:'CNN Sans Display',Helvetica Neue,Helvetica,Arial,Utkal,sans-serif}@font-fac

In [26]:
story_str000_bs = BeautifulSoup(story_str000, 'html.parser')
rex_art = rex.compile(r'articleBody[\S\s]*\",')
rex_art.findall(story_str000)

['articleBody":"The credit ratings of US mortgage giants Freddie Mac and Fannie Mae were put on watch for possible downgrade by Fitch Ratings late Thursday. A downgrade is not expected to happen, as a deal to resolve the debt ceiling standoff continues to be worked out in Washington, but even the warning is having an impact on mortgage rates. The warning came because the ratings for Fannie Mae and Freddie Mac are linked to the sovereign rating of the United States. The watch is a result of the ratings agency warning on Wednesday that America’s credit rating could be downgraded if the debt limit showdown was not resolved soon.   Fannie and Freddie, which guarantee roughly 70% of the country’s mortgages, do not directly issue mortgages to borrowers, but instead buy mortgages from lenders and repackage them for investors. They are each a government-sponsored enterprise, or GSE, chartered by Congress. The aim of Freddie and Fannie is to provide liquidity into the mortgage market and enable

In [14]:
story_str000_bs.find(class_='articleBody')

In [10]:
story_str100 = df['article_text'][100]
print(story_str100)

<!DOCTYPE html>
<html data-n-head="%7B%22lang%22:%7B%22ssr%22:%22en%22%7D%7D" data-n-head-ssr="" lang="en">
 <head>
  <title>
   Bronny James faces nasty comments on social media over prom date | Fox News
  </title>
  <meta content="IE=edge,chrome=1" data-n-head="ssr" http-equiv="X-UA-Compatible"/>
  <meta content="text/html; charset=utf-8" data-hid="content-type" data-n-head="ssr" http-equiv="content-type"/>
  <meta content="on" data-hid="x-dns-prefetch-control" data-n-head="ssr" http-equiv="x-dns-prefetch-control"/>
  <meta charset="utf-8" data-n-head="ssr"/>
  <meta content="width=device-width, minimum-scale=1.0, initial-scale=1.0" data-hid="viewport" data-n-head="ssr" name="viewport"/>
  <meta content="en" data-hid="content-language" data-n-head="ssr" http-equiv="content-language"/>
  <meta content="Bronny James, the son of Los Angeles Lakers superstar LeBron James, faced nastiness online as he took his date to his final high school prom." data-hid="description" data-n-head="ssr" n

In [20]:
rex_art100 = rex.compile(r'articleBody[\S\s]+}')
rex_art100.findall(story_str100)

['articleBody": "Bronny James, the son of LeBron James who is set to attend USC to further his basketball career, attended prom over the weekend with his rumored girlfriend, Peyton Gelfuso, as his high school days come to an end. The Sierra Canyon High School senior wore a black Chrome Hearts suit with Dior shoes for the night, according to the New York Post. Multiple photos surfaced online showing James posing with his mother, Savannah, and Gelfuso looking dapper as he went to potentially his final prom. Savannah James posted photos on her social media with the caption, \\"Lost for words.\\" CLICK HERE FOR MORE SPORTS COVERAGE ON FOXNEWS.COM  The USC commit’s photos were plastered across Instagram over the course of the week, and some appeared to be upset with James taking Gelfuso to the prom because she is White.  \\"Well he is following in the footsteps of many other athletes with the white chick on his arm,\\" Instagram user @fantabulous_lisa wrote. \\"Don’t get finessed young king

print(df.head())
print(df['article_text'][100])

### Commit changes and close cursor and connection instances

In [12]:
# Commit the changes to the database
db_conn.commit()

# Close the cursor and database connection
cursor.close()
db_conn.close()